# Get isodistances from API
https://docs.graphhopper.com/#tag/Isochrone-API

In [1]:
import requests
import pandas as pd
import geopandas as gpd
import numpy as np
from shapely.geometry import Polygon
import folium
import time

In [2]:
# load park entrances in dataframe
entrances_df = pd.read_json('../get_park_data/total_park_entrances.json')
# load park list with distances in dataframe
distances_df = pd.read_json('../get_park_data/distance_data.json', orient='index')
entrances_df.head()

name        lat      long
0  Luusbarg  53.570125  9.761084
1  Luusbarg  53.570329  9.761556
2  Luusbarg  53.568481  9.760017
3  Luusbarg  53.568468  9.759341
4  Luusbarg  53.567232  9.759298

In [3]:
# walking distances added to park entrances
park_entrances=entrances_df.merge(distances_df, how='left', on = 'name')
park_entrances.head()

name        lat      long  walk_dist
0  Luusbarg  53.570125  9.761084        500
1  Luusbarg  53.570329  9.761556        500
2  Luusbarg  53.568481  9.760017        500
3  Luusbarg  53.568468  9.759341        500
4  Luusbarg  53.567232  9.759298        500

In [4]:
park_entrances_500 = park_entrances[park_entrances["walk_dist"] == 500]
park_entrances_1000 = park_entrances[park_entrances["walk_dist"] == 1000]
park_entrances_1500 = park_entrances[park_entrances["walk_dist"] == 1500]
park_entrances_500.head()

name        lat      long  walk_dist
0  Luusbarg  53.570125  9.761084        500
1  Luusbarg  53.570329  9.761556        500
2  Luusbarg  53.568481  9.760017        500
3  Luusbarg  53.568468  9.759341        500
4  Luusbarg  53.567232  9.759298        500

In [5]:
# Define Function for API Request
def api_request(coordinates,distance_limit):
  url = "https://graphhopper.com/api/1/isochrone"

  query = {
    "point": coordinates,
    "time_limit": "",
    "distance_limit": distance_limit,
    "profile": "foot",
    "buckets": "1",
    "reverse_flow": "false",
    "key": "726e0e38-9740-49b0-9b98-583e94de98a0"
  }

  response = requests.get(url, params=query)
  time.sleep(3)
  data = response.json()
  return data

In [6]:
# define function for transforming data and adding to dataframe
def add_to_df(name, isodistance, tmp_df):
    coordinates = isodistance['polygons'][0]['geometry']['coordinates'][0]
    geometry = Polygon(coordinates)
    dict = {'name': name, 'geometry': gpd.GeoSeries(geometry)}
    tmp_df = pd.concat([tmp_df, pd.DataFrame(dict)])
    return tmp_df


In [7]:
test = park_entrances_1500.head(5)
test.head()

name        lat      long  walk_dist
67  Waldpark Marienhoehe  53.577763  9.772183       1500
68  Waldpark Marienhoehe  53.578066  9.772419       1500
69  Waldpark Marienhoehe  53.576948  9.774452       1500
70  Waldpark Marienhoehe  53.576700  9.775203       1500
71  Waldpark Marienhoehe  53.576126  9.777011       1500

In [8]:
# Define Function for iterating over park entrance dataframe
def get_isodistances(park_entrances):
    tmp_df = pd.DataFrame(columns =[ "name", "geometry"])
    for entrance in park_entrances.itertuples():
        name = entrance.name
        lat = entrance.lat
        long = entrance.long
        walking_distance = entrance.walk_dist
        coordinates = f"{lat},{long}"

        # api request
        isodistance = api_request(coordinates,walking_distance)
        print(f"Isodistance API request made for park entrance at {coordinates} of {name} with a walking distance of {walking_distance}m.")
        print(isodistance)
        # add to dataframe
        df = add_to_df(name,isodistance, tmp_df)
        tmp_df = df
        time.sleep(5)
    gdf = gpd.GeoDataFrame(tmp_df,geometry='geometry')
    return gdf

In [225]:
test_ = get_isodistances(test)
test_.head()

Isodistance API request made for park entrance at 53.577763313665294,9.772183299064638 of Waldpark Marienhoehe with a walking distance of 1500m.
Isodistance API request made for park entrance at 53.578065889718324,9.772419333457949 of Waldpark Marienhoehe with a walking distance of 1500m.
Isodistance API request made for park entrance at 53.57694794004697,9.774452447891237 of Waldpark Marienhoehe with a walking distance of 1500m.
Isodistance API request made for park entrance at 53.57669950277199,9.775203466415407 of Waldpark Marienhoehe with a walking distance of 1500m.
Isodistance API request made for park entrance at 53.57612618041178,9.777011275291445 of Waldpark Marienhoehe with a walking distance of 1500m.


name                                           geometry
0  Waldpark Marienhoehe  POLYGON ((9.77659 53.58148, 9.77649 53.58148, ...
0  Waldpark Marienhoehe  POLYGON ((9.77730 53.58149, 9.77695 53.58148, ...
0  Waldpark Marienhoehe  POLYGON ((9.77659 53.58148, 9.77649 53.58148, ...
0  Waldpark Marienhoehe  POLYGON ((9.77574 53.58070, 9.77554 53.58073, ...
0  Waldpark Marienhoehe  POLYGON ((9.77574 53.58070, 9.77554 53.58073, ...

In [ ]:
map = folium.Map(location=[53.41535, 9.90225], tiles="CartoDB Positron", zoom_start=11, control_scale = True)
for _, r in test_.iterrows():
    sim_geo = gpd.GeoSeries(r["geometry"])
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j, style_function=lambda x: {"fillColor": "orange"})
    folium.Popup(r["name"]).add_to(geo_j)
    geo_j.add_to(map)


map

In [256]:
park_entrances_1000.head(1000)

name        lat       long  walk_dist
17          Waldpark Falkenstein  53.565279   9.763863       1000
18          Waldpark Falkenstein  53.564891   9.765397       1000
19          Waldpark Falkenstein  53.564916   9.766170       1000
20          Waldpark Falkenstein  53.564521   9.768085       1000
21          Waldpark Falkenstein  53.563693   9.771937       1000
...                          ...        ...        ...        ...
1129  Gruenes Zentrum Lohbruegge  53.504139  10.210419       1000
1130  Gruenes Zentrum Lohbruegge  53.508759  10.210311       1000
1131  Gruenes Zentrum Lohbruegge  53.510839  10.205591       1000
1132  Gruenes Zentrum Lohbruegge  53.510686  10.204840       1000
1133  Gruenes Zentrum Lohbruegge  53.509167  10.204067       1000

[332 rows x 4 columns]

In [257]:
isodistances_1000 = get_isodistances(park_entrances_1000)

Isodistance API request made for park entrance at 53.56527936780528,9.763863086700441 of Waldpark Falkenstein with a walking distance of 1000m.
{'polygons': [{'type': 'Feature', 'geometry': {'type': 'Polygon', 'coordinates': [[[9.770903350000001, 53.565512], [9.76994285, 53.56574635], [9.7698486, 53.5663432], [9.7699157, 53.566495599999996], [9.770493349999999, 53.56698585], [9.771016, 53.5666012], [9.77177195, 53.566458350000005], [9.7718742, 53.566570600000006], [9.7719254, 53.5668372], [9.772403650000001, 53.5672661], [9.7729085, 53.5671733], [9.7729699, 53.56706815], [9.773457650000001, 53.5669503], [9.77458945, 53.5673052], [9.7747385, 53.5677729], [9.7743442, 53.568995900000004], [9.77384365, 53.56912785], [9.77346925, 53.56919205], [9.7733309, 53.5697361], [9.77309125, 53.56976865], [9.7730734, 53.569855849999996], [9.7721165, 53.57078605], [9.772248900000001, 53.57122475], [9.7709858, 53.573388], [9.770430600000001, 53.57329765], [9.769729000000002, 53.5734217], [9.76832925, 53

In [268]:

isodistances_1000.to_file('isodistances_1000.json', driver ='GeoJSON')


In [9]:
park_entrances_500 = park_entrances_500.sort_values(by='name', ascending= True)
park_entrances_500

name        lat      long  walk_dist
422     Alsenpark  53.565241  9.945948        500
428     Alsenpark  53.566073  9.950647        500
427     Alsenpark  53.565955  9.950920        500
426     Alsenpark  53.565477  9.949504        500
425     Alsenpark  53.565235  9.947847        500
..            ...        ...       ...        ...
948  Wohlers Park  53.559117  9.951038        500
949  Wohlers Park  53.559161  9.953495        500
950  Wohlers Park  53.558129  9.954568        500
952  Wohlers Park  53.557186  9.951768        500
951  Wohlers Park  53.557294  9.953152        500

[723 rows x 4 columns]

In [10]:
isodistances_500 = get_isodistances(park_entrances_500)

Isodistance API request made for park entrance at 53.56524113623294,9.945947527885439 of Alsenpark with a walking distance of 500m.
{'polygons': [{'type': 'Feature', 'geometry': {'type': 'Polygon', 'coordinates': [[[9.94882755, 53.56328185], [9.9494203, 53.56341135], [9.94942835, 53.5631489], [9.949514449999999, 53.563126], [9.949563999999999, 53.563112849999996], [9.9496814, 53.563135700000004], [9.94971365, 53.563163349999996], [9.9498794, 53.56314795], [9.9500636, 53.563342399999996], [9.9502715, 53.5630822], [9.9507384, 53.56304815], [9.950908, 53.5631349], [9.9510155, 53.5631944], [9.95116615, 53.56324725], [9.951454250000001, 53.56351875], [9.9514763, 53.563729249999994], [9.951453749999999, 53.5637422], [9.951097749999999, 53.56381705], [9.950969650000001, 53.563751249999996], [9.9508702, 53.563756600000005], [9.9508163, 53.5637708], [9.9507424, 53.56381295], [9.950692199999999, 53.563853949999995], [9.95065885, 53.563919299999995], [9.9504085, 53.5639688], [9.9503943, 53.564106

In [12]:
isodistances_500.to_file('isodistances_500.json', driver ='GeoJSON')

In [13]:
isodistances_1500 = get_isodistances(park_entrances_1500)

Isodistance API request made for park entrance at 53.577763313665294,9.772183299064638 of Waldpark Marienhoehe with a walking distance of 1500m.
{'polygons': [{'type': 'Feature', 'geometry': {'type': 'Polygon', 'coordinates': [[[9.77659055, 53.581476550000005], [9.776490899999999, 53.58147785], [9.776427649999999, 53.581474650000004], [9.776392600000001, 53.58147375], [9.7763011, 53.581472950000006], [9.77623295, 53.58147375], [9.775769, 53.5812599], [9.7753062, 53.5812666], [9.77497455, 53.581274449999995], [9.7749565, 53.58127475], [9.77476015, 53.5813104], [9.7742541, 53.581156], [9.7734211, 53.5811872], [9.773392300000001, 53.58119715], [9.77283985, 53.5812864], [9.7724936, 53.5809957], [9.77223155, 53.58101345], [9.771788, 53.5810435], [9.771414799999999, 53.5814754], [9.7712109, 53.581493800000004], [9.77056665, 53.58120415], [9.769745149999999, 53.5812847], [9.7689548, 53.58133435], [9.76894525, 53.58203345], [9.76865205, 53.582464099999996], [9.76864055, 53.5828089], [9.7683539

In [15]:
isodistances_1500.to_file('isodistances_1500.json', driver ='GeoJSON')